Copyright **`(c)`** 2025 Giovanni Squillero `<giovanni.squillero@polito.it>`  
[`https://github.com/squillero/computational-intelligence`](https://github.com/squillero/computational-intelligence)  
Free under certain conditions — see the [`license`](https://github.com/squillero/computational-intelligence/blob/master/LICENSE.md) for details.  

In [428]:
from itertools import product, combinations, permutations
import numpy as np
import networkx as nx
from icecream import ic
import matplotlib.pyplot as plt
from tqdm import tqdm

In [429]:
def create_problem(
    size: int,
    *,
    density: float = 1.0,
    negative_values: bool = False,
    noise_level: float = 0.0,
    seed: int = 50,
) -> np.ndarray:
    """Problem generator for Lab3"""
    rng = np.random.default_rng(seed)
    map = rng.random(size=(size, 2))
    problem = rng.random((size, size))
    if negative_values:
        problem = problem * 2 - 1
    problem *= noise_level
    for a, b in product(range(size), repeat=2):
        if rng.random() < density:
            problem[a, b] += np.sqrt(
                np.square(map[a, 0] - map[b, 0]) + np.square(map[a, 1] - map[b, 1])
            )
        else:
            problem[a, b] = np.inf
    np.fill_diagonal(problem, 0)
    return (problem * 1_000).round()

In [430]:
##### HELPER METHODS #####

def generateNodesPermutations(problem: nx.DiGraph):
    result = []
    for s, d in permutations(range(len(list(problem.nodes))), 2):
        result.append([s, d])
    return result


# this is the same code by the prof, i just repurposed it
def solveWithBellmanFord(graph, s, d):
    try:
        path = nx.bellman_ford_path(graph, s, d, weight='weight')
        cost = cost = nx.path_weight(graph, path, weight='weight')
        err = ''
    except nx.NetworkXNoPath:
        # Nodes are not connected
        err = 'unconnected'
        path = None
        cost = np.inf
    except nx.NetworkXUnbounded:
        # Negative cycle detected
        err = 'negative cycle'
        path = None
        cost = -np.inf
    return s, d, path, cost, err

# THIS WILL TAKE SOME TIME


def generateAllProblems():
    availableParameters = [
        [10, 20, 50, 100, 200, 500, 1000],  # size
        [0.2, 0.5, 0.8, 1.0],  # density
        [0.0, 0.1, 0.5, 0.8],  # noise_level
        [False, True]  # negative_values
    ]
    combinationsOfParameters = list(product(*availableParameters))
    results = []
    # a nice idea for testing is to not take all the possible combinations
    # for parameters in combinationsOfParameters[5:10]:
    for parameters in combinationsOfParameters[50:60]:
        createdProblem = create_problem(
            parameters[0],
            density=parameters[1],
            noise_level=parameters[2],
            negative_values=parameters[3])
        masked = np.ma.masked_array(
            createdProblem, mask=np.isinf(createdProblem))
        G = nx.from_numpy_array(masked, create_using=nx.DiGraph)
        nodes = G.number_of_nodes()
        edges = G.number_of_edges()
        edgeList = list(G.edges(data=True))
        ic(parameters, nodes, edges, edgeList, createdProblem)
        # send back also the parameters so we can know which parameters created that problem
        results.append([parameters, G])

    return results

In [431]:
problems = generateAllProblems()
bellmanStats = {}

for [parameters, graph] in problems:
    ic('')
    ic('################### new solution #########################')
    ic(parameters)
    bellmanStats[parameters] = 0
    for [s, d] in generateNodesPermutations(graph):
        bellmanSolution = ic(solveWithBellmanFord(graph, s, d))
        bellmanStats[parameters] += 1 if bellmanSolution[2] != None else 0

bellmanStats

ic| parameters: (20, 0.8, 0.1, False)
    nodes: 20
    edges: 311
    edgeList: [(0, 2, {'weight': 582.0}),
               (0, 4, {'weight': 779.0}),
               (0, 5, {'weight': 515.0}),
               (0, 6, {'weight': 891.0}),
               (0, 8, {'weight': 297.0}),
               (0, 9, {'weight': 851.0}),
               (0, 10, {'weight': 679.0}),
               (0, 11, {'weight': 796.0}),
               (0, 14, {'weight': 424.0}),
               (0, 15, {'weight': 759.0}),
               (0, 16, {'weight': 270.0}),
               (0, 17, {'weight': 889.0}),
               (0, 18, {'weight': 702.0}),
               (1, 2, {'weight': 454.0}),
               (1, 3, {'weight': 659.0}),
               (1, 4, {'weight': 778.0}),
               (1, 6, {'weight': 963.0}),
               (1, 7, {'weight': 479.0}),
               (1, 8, {'weight': 137.0}),
               (1, 9, {'weight': 699.0}),
               (1, 10, {'weight': 700.0}),
               (1, 11, {'weight': 970.0}),


{(20, 0.8, 0.1, False): 380,
 (20, 0.8, 0.1, True): 380,
 (20, 0.8, 0.5, False): 380,
 (20, 0.8, 0.5, True): 0,
 (20, 0.8, 0.8, False): 380,
 (20, 0.8, 0.8, True): 0,
 (20, 1.0, 0.0, False): 380,
 (20, 1.0, 0.0, True): 380,
 (20, 1.0, 0.1, False): 380,
 (20, 1.0, 0.1, True): 380}